In [2]:
#-*-coding:utf8-*-

"""
author:YJM

date:20190420

util function

"""
import os
import sys
import numpy as np
import pandas as pd
import operator

In [4]:
def get_graph_from_data(input_file):
    """
    Args:
        input_file:user item rating file
    Return:
        a dict:{User A:{itemb:1,itemc:1},itemb:{UserA:1}}
    """
    if not os.path.exists(input_file):
        return {}
    graph={}
    linenum =0
    score_thr=4.0
    fp = open(input_file)
    for line in fp:
        if linenum ==0:
            linenum +=1
            continue
        item = line.strip().split(",")
        if len(item)<3:
            continue
        userid,itemid,rating =item[0],"item_"+item[1],item[2]
        if float(rating)<score_thr:
            continue
        if userid not in graph:
            graph[userid] ={}
        graph[userid][itemid]=1
        if itemid not in graph:
            graph[itemid]={}
        graph[itemid][userid] = 1
    fp.close()
    return graph

In [6]:
get_data=get_graph_from_data("../data/ratings15000.csv")
# print(get_data)

In [ ]:
def personal_rank(graph,alpha,)

### 通过movies.csv获取电影信息

In [2]:
def get_item_info(input_file):
    if not os.path.exists(input_file):
        return {}
    item_info={}
    linenum=0
    fp = open(input_file)
    for line in fp:
        if linenum == 0:
            linenum += 1
            continue
        item = line.strip().split(',')
        if len(item)<3:
            continue
        elif len(item) == 3:
            itemid,title,genre = item[0],item[1],item[2]
        elif len(item)>3:
            itemid = item[0]
            genre = item[-1]
            title = ','.join(item[1:-1])
        item_info[itemid]=[title,genre]
    fp.closed
    return item_info

### 通过ratings15000.csv获取平均分

In [3]:
def get_ave_score(input_file):
    if not os.path.exists(input_file):
        return {}
    linenum = 0
    record_dict = {}
    score_dict = {}
    fp = open(input_file)
    for line in fp:
        if linenum == 0:
            linenum += 1
            continue
        item = line.strip().split(',')
        if len(item)<4:
            continue
        userid,itemid,rating = item[0],item[1],float(item[2])
        if itemid not in record_dict:
            record_dict[itemid]=[0,0]
        record_dict[itemid][0] += 1
        record_dict[itemid][1] += rating
    fp.closed
    for itemid in record_dict:
        score_dict[itemid] = round(record_dict[itemid][1]/record_dict[itemid][0],3)#小数点后保留3位有效数字
    return score_dict

### 获取数据

In [4]:
def get_train_data(input_file):
    """
    :param input_file:
    input_file:user item rating file
    :return:
    alist:[(userid,itemid,label),(userid,itemid,label)]
    """
    if not os.path.exists(input_file):
        return {}
    score_dict = get_ave_score(input_file)#通过前面的方法获取平均分
    neg_dict = {}#负样本集合
    pos_dict = {}#正样本集合
    train_data = []
    linenum = 0
    score_thr = 4#正负分界线：4分
    fp = open(input_file)
    for line in fp:
        if linenum == 0:
            linenum += 1
            continue
        item = line.strip().split(',')
        if len(item)<4:
            continue
        userid,itemid,rating = item[0],item[1],float(item[2])
        if userid not in pos_dict:
            pos_dict[userid] = []
        if userid not in neg_dict:
            neg_dict[userid] = []
        if rating >=score_thr:
            pos_dict[userid].append((itemid,1))#这里正样本的格式是（userid，itemid，1）1代表正样本
        else:
            score = score_dict.get(itemid,0)#如果平均分没有获取到就设置成0
            neg_dict[userid].append((itemid,score))#这里负样本的格式是（userid，itemid，平均得分）    
    fp.closed
    for userid in pos_dict:
        data_num = min(len(pos_dict[userid]),len(neg_dict.get(userid,[])))
        if data_num > 0:
            train_data += [(userid,zuhe[0],zuhe[1]) for zuhe in pos_dict[userid]][:data_num]
        else:
            continue
        #将负样本倒序排好并且取和正样本同样大小的样本集合
        sorted_neg_list = sorted(neg_dict[userid],key=lambda element:element[1], reverse=True)[:data_num]
        train_data += [(userid,zuhe[0],0)for zuhe in sorted_neg_list]#将最后一个值替换成0
    return train_data

### 将personalRank的模型进行训练

In [5]:
def lfm_train(train_data,F,alpha,beta,step):
    user_vec = {}
    item_vec = {}
    for step_index in range(step):#迭代轮次
        for data_instance in train_data:
            userid,itemid,label = data_instance
            if userid not in user_vec:
                user_vec[userid] = init_model(F)
            if itemid not in item_vec:
                item_vec[itemid] = init_model(F)
            delta = label - model_predict(user_vec[userid],item_vec[itemid])
            for index in range(F):
                user_vec[userid][index] += beta*(delta*item_vec[itemid][index]-alpha*user_vec[userid][index])
                item_vec[itemid][index] += beta*(delta*user_vec[userid][index]-alpha*item_vec[itemid][index])
            beta = beta*0.9      #学习率衰减
    return user_vec,item_vec

### 初始化模型

In [6]:
def init_model(vector_len):
    """
        vector_len:the len of vector
    """
    return np.random.randn(vector_len)

### 计算用户向量和物品向量的余弦夹角

In [7]:
def model_predict(user_vector,item_vector):
    res = np.dot(user_vector,item_vector)/(np.linalg.norm(user_vector)*np.linalg.norm(item_vector))
    return res

### 模型训练函数

In [8]:
def model_train_process():
    train_data = get_train_data("../data/ratings15000.csv")
    user_vec,item_vec = lfm_train(train_data,50,0.01,0.1,50)
    recom_result = give_recom_result(user_vec,item_vec,'24')
    print recom_result
    ana_recom_result(train_data,'24',recom_result)

### 模型训练执行

In [12]:
model_train_process()

[('58315', 22.924), ('7160', 22.804), ('2021', 21.72), ('40732', 21.259), ('6158', 20.454), ('3809', 20.375), ('1635', 20.333), ('6794', 20.12), ('1043', 19.491), ('33136', 18.911)]
['Toy Story (1995)', 'Adventure|Animation|Children|Comedy|Fantasy']
recom result
['"Love Guru, The (2008)"', '"Love Guru']
['Monster (2003)', 'Crime|Drama']
['Dune (1984)', 'Adventure|Sci-Fi']
['"Descent, The (2005)"', '"Descent']
['"Jungle Book 2, The (2003)"', '"Jungle Book 2']
['What About Bob? (1991)', 'Comedy']
['"Ice Storm, The (1997)"', '"Ice Storm']
["Beethoven's 2nd (1993)", 'Children|Comedy']
['To Gillian on Her 37th Birthday (1996)', 'Drama|Romance']
['House of D (2004)', 'Drama']
['Heat (1995)', 'Action|Crime|Thriller']
recom result
['"Love Guru, The (2008)"', '"Love Guru']
['Monster (2003)', 'Crime|Drama']
['Dune (1984)', 'Adventure|Sci-Fi']
['"Descent, The (2005)"', '"Descent']
['"Jungle Book 2, The (2003)"', '"Jungle Book 2']
['What About Bob? (1991)', 'Comedy']
['"Ice Storm, The (1997)"', '"

['House of D (2004)', 'Drama']
['Beavis and Butt-Head Do America (1996)', 'Adventure|Animation|Comedy|Crime']
recom result
['"Love Guru, The (2008)"', '"Love Guru']
['Monster (2003)', 'Crime|Drama']
['Dune (1984)', 'Adventure|Sci-Fi']
['"Descent, The (2005)"', '"Descent']
['"Jungle Book 2, The (2003)"', '"Jungle Book 2']
['What About Bob? (1991)', 'Comedy']
['"Ice Storm, The (1997)"', '"Ice Storm']
["Beethoven's 2nd (1993)", 'Children|Comedy']
['To Gillian on Her 37th Birthday (1996)', 'Drama|Romance']
['House of D (2004)', 'Drama']
['Scream (1996)', 'Comedy|Horror|Mystery|Thriller']
recom result
['"Love Guru, The (2008)"', '"Love Guru']
['Monster (2003)', 'Crime|Drama']
['Dune (1984)', 'Adventure|Sci-Fi']
['"Descent, The (2005)"', '"Descent']
['"Jungle Book 2, The (2003)"', '"Jungle Book 2']
['What About Bob? (1991)', 'Comedy']
['"Ice Storm, The (1997)"', '"Ice Storm']
["Beethoven's 2nd (1993)", 'Children|Comedy']
['To Gillian on Her 37th Birthday (1996)', 'Drama|Romance']
['House of 

['"Jungle Book 2, The (2003)"', '"Jungle Book 2']
['What About Bob? (1991)', 'Comedy']
['"Ice Storm, The (1997)"', '"Ice Storm']
["Beethoven's 2nd (1993)", 'Children|Comedy']
['To Gillian on Her 37th Birthday (1996)', 'Drama|Romance']
['House of D (2004)', 'Drama']
['Saving Silverman (Evil Woman) (2001)', 'Comedy|Romance']
recom result
['"Love Guru, The (2008)"', '"Love Guru']
['Monster (2003)', 'Crime|Drama']
['Dune (1984)', 'Adventure|Sci-Fi']
['"Descent, The (2005)"', '"Descent']
['"Jungle Book 2, The (2003)"', '"Jungle Book 2']
['What About Bob? (1991)', 'Comedy']
['"Ice Storm, The (1997)"', '"Ice Storm']
["Beethoven's 2nd (1993)", 'Children|Comedy']
['To Gillian on Her 37th Birthday (1996)', 'Drama|Romance']
['House of D (2004)', 'Drama']
['Down to Earth (2001)', 'Comedy|Fantasy|Romance']
recom result
['"Love Guru, The (2008)"', '"Love Guru']
['Monster (2003)', 'Crime|Drama']
['Dune (1984)', 'Adventure|Sci-Fi']
['"Descent, The (2005)"', '"Descent']
['"Jungle Book 2, The (2003)"', 

['To Gillian on Her 37th Birthday (1996)', 'Drama|Romance']
['House of D (2004)', 'Drama']
recom result
['"Love Guru, The (2008)"', '"Love Guru']
['Monster (2003)', 'Crime|Drama']
['Dune (1984)', 'Adventure|Sci-Fi']
['"Descent, The (2005)"', '"Descent']
['"Jungle Book 2, The (2003)"', '"Jungle Book 2']
['What About Bob? (1991)', 'Comedy']
['"Ice Storm, The (1997)"', '"Ice Storm']
["Beethoven's 2nd (1993)", 'Children|Comedy']
['To Gillian on Her 37th Birthday (1996)', 'Drama|Romance']
['House of D (2004)', 'Drama']
recom result
['"Love Guru, The (2008)"', '"Love Guru']
['Monster (2003)', 'Crime|Drama']
['Dune (1984)', 'Adventure|Sci-Fi']
['"Descent, The (2005)"', '"Descent']
['"Jungle Book 2, The (2003)"', '"Jungle Book 2']
['What About Bob? (1991)', 'Comedy']
['"Ice Storm, The (1997)"', '"Ice Storm']
["Beethoven's 2nd (1993)", 'Children|Comedy']
['To Gillian on Her 37th Birthday (1996)', 'Drama|Romance']
['House of D (2004)', 'Drama']
recom result
['"Love Guru, The (2008)"', '"Love Gur

['To Gillian on Her 37th Birthday (1996)', 'Drama|Romance']
['House of D (2004)', 'Drama']
recom result
['"Love Guru, The (2008)"', '"Love Guru']
['Monster (2003)', 'Crime|Drama']
['Dune (1984)', 'Adventure|Sci-Fi']
['"Descent, The (2005)"', '"Descent']
['"Jungle Book 2, The (2003)"', '"Jungle Book 2']
['What About Bob? (1991)', 'Comedy']
['"Ice Storm, The (1997)"', '"Ice Storm']
["Beethoven's 2nd (1993)", 'Children|Comedy']
['To Gillian on Her 37th Birthday (1996)', 'Drama|Romance']
['House of D (2004)', 'Drama']
recom result
['"Love Guru, The (2008)"', '"Love Guru']
['Monster (2003)', 'Crime|Drama']
['Dune (1984)', 'Adventure|Sci-Fi']
['"Descent, The (2005)"', '"Descent']
['"Jungle Book 2, The (2003)"', '"Jungle Book 2']
['What About Bob? (1991)', 'Comedy']
['"Ice Storm, The (1997)"', '"Ice Storm']
["Beethoven's 2nd (1993)", 'Children|Comedy']
['To Gillian on Her 37th Birthday (1996)', 'Drama|Romance']
['House of D (2004)', 'Drama']
recom result
['"Love Guru, The (2008)"', '"Love Gur

...

['Monster (2003)', 'Crime|Drama']
['Dune (1984)', 'Adventure|Sci-Fi']
['"Descent, The (2005)"', '"Descent']
['"Jungle Book 2, The (2003)"', '"Jungle Book 2']
['What About Bob? (1991)', 'Comedy']
['"Ice Storm, The (1997)"', '"Ice Storm']
["Beethoven's 2nd (1993)", 'Children|Comedy']
['To Gillian on Her 37th Birthday (1996)', 'Drama|Romance']
['House of D (2004)', 'Drama']
recom result
['"Love Guru, The (2008)"', '"Love Guru']
['Monster (2003)', 'Crime|Drama']
['Dune (1984)', 'Adventure|Sci-Fi']
['"Descent, The (2005)"', '"Descent']
['"Jungle Book 2, The (2003)"', '"Jungle Book 2']
['What About Bob? (1991)', 'Comedy']
['"Ice Storm, The (1997)"', '"Ice Storm']
["Beethoven's 2nd (1993)", 'Children|Comedy']
['To Gillian on Her 37th Birthday (1996)', 'Drama|Romance']
['House of D (2004)', 'Drama']
recom result
['"Love Guru, The (2008)"', '"Love Guru']
['Monster (2003)', 'Crime|Drama']
['Dune (1984)', 'Adventure|Sci-Fi']
['"Descent, The (2005)"', '"Descent']
['"Jungle Book 2, The (2003)"', '"

['House of D (2004)', 'Drama']
recom result
['"Love Guru, The (2008)"', '"Love Guru']
['Monster (2003)', 'Crime|Drama']
['Dune (1984)', 'Adventure|Sci-Fi']
['"Descent, The (2005)"', '"Descent']
['"Jungle Book 2, The (2003)"', '"Jungle Book 2']
['What About Bob? (1991)', 'Comedy']
['"Ice Storm, The (1997)"', '"Ice Storm']
["Beethoven's 2nd (1993)", 'Children|Comedy']
['To Gillian on Her 37th Birthday (1996)', 'Drama|Romance']
['House of D (2004)', 'Drama']
recom result
['"Love Guru, The (2008)"', '"Love Guru']
['Monster (2003)', 'Crime|Drama']
['Dune (1984)', 'Adventure|Sci-Fi']
['"Descent, The (2005)"', '"Descent']
['"Jungle Book 2, The (2003)"', '"Jungle Book 2']
['What About Bob? (1991)', 'Comedy']
['"Ice Storm, The (1997)"', '"Ice Storm']
["Beethoven's 2nd (1993)", 'Children|Comedy']
['To Gillian on Her 37th Birthday (1996)', 'Drama|Romance']
['House of D (2004)', 'Drama']
recom result
['"Love Guru, The (2008)"', '"Love Guru']
['Monster (2003)', 'Crime|Drama']
['Dune (1984)', 'Adven

['To Gillian on Her 37th Birthday (1996)', 'Drama|Romance']
['House of D (2004)', 'Drama']
recom result
['"Love Guru, The (2008)"', '"Love Guru']
['Monster (2003)', 'Crime|Drama']
['Dune (1984)', 'Adventure|Sci-Fi']
['"Descent, The (2005)"', '"Descent']
['"Jungle Book 2, The (2003)"', '"Jungle Book 2']
['What About Bob? (1991)', 'Comedy']
['"Ice Storm, The (1997)"', '"Ice Storm']
["Beethoven's 2nd (1993)", 'Children|Comedy']
['To Gillian on Her 37th Birthday (1996)', 'Drama|Romance']
['House of D (2004)', 'Drama']
recom result
['"Love Guru, The (2008)"', '"Love Guru']
['Monster (2003)', 'Crime|Drama']
['Dune (1984)', 'Adventure|Sci-Fi']
['"Descent, The (2005)"', '"Descent']
['"Jungle Book 2, The (2003)"', '"Jungle Book 2']
['What About Bob? (1991)', 'Comedy']
['"Ice Storm, The (1997)"', '"Ice Storm']
["Beethoven's 2nd (1993)", 'Children|Comedy']
['To Gillian on Her 37th Birthday (1996)', 'Drama|Romance']
['House of D (2004)', 'Drama']
recom result
['"Love Guru, The (2008)"', '"Love Gur

['"Jungle Book 2, The (2003)"', '"Jungle Book 2']
['What About Bob? (1991)', 'Comedy']
['"Ice Storm, The (1997)"', '"Ice Storm']
["Beethoven's 2nd (1993)", 'Children|Comedy']
['To Gillian on Her 37th Birthday (1996)', 'Drama|Romance']
['House of D (2004)', 'Drama']
recom result
['"Love Guru, The (2008)"', '"Love Guru']
['Monster (2003)', 'Crime|Drama']
['Dune (1984)', 'Adventure|Sci-Fi']
['"Descent, The (2005)"', '"Descent']
['"Jungle Book 2, The (2003)"', '"Jungle Book 2']
['What About Bob? (1991)', 'Comedy']
['"Ice Storm, The (1997)"', '"Ice Storm']
["Beethoven's 2nd (1993)", 'Children|Comedy']
['To Gillian on Her 37th Birthday (1996)', 'Drama|Romance']
['House of D (2004)', 'Drama']
recom result
['"Love Guru, The (2008)"', '"Love Guru']
['Monster (2003)', 'Crime|Drama']
['Dune (1984)', 'Adventure|Sci-Fi']
['"Descent, The (2005)"', '"Descent']
['"Jungle Book 2, The (2003)"', '"Jungle Book 2']
['What About Bob? (1991)', 'Comedy']
['"Ice Storm, The (1997)"', '"Ice Storm']
["Beethoven's

['What About Bob? (1991)', 'Comedy']
['"Ice Storm, The (1997)"', '"Ice Storm']
["Beethoven's 2nd (1993)", 'Children|Comedy']
['To Gillian on Her 37th Birthday (1996)', 'Drama|Romance']
['House of D (2004)', 'Drama']
recom result
['"Love Guru, The (2008)"', '"Love Guru']
['Monster (2003)', 'Crime|Drama']
['Dune (1984)', 'Adventure|Sci-Fi']
['"Descent, The (2005)"', '"Descent']
['"Jungle Book 2, The (2003)"', '"Jungle Book 2']
['What About Bob? (1991)', 'Comedy']
['"Ice Storm, The (1997)"', '"Ice Storm']
["Beethoven's 2nd (1993)", 'Children|Comedy']
['To Gillian on Her 37th Birthday (1996)', 'Drama|Romance']
['House of D (2004)', 'Drama']
recom result
['"Love Guru, The (2008)"', '"Love Guru']
['Monster (2003)', 'Crime|Drama']
['Dune (1984)', 'Adventure|Sci-Fi']
['"Descent, The (2005)"', '"Descent']
['"Jungle Book 2, The (2003)"', '"Jungle Book 2']
['What About Bob? (1991)', 'Comedy']
['"Ice Storm, The (1997)"', '"Ice Storm']
["Beethoven's 2nd (1993)", 'Children|Comedy']
['To Gillian on H

### 推荐过程

In [10]:
def give_recom_result(user_vec,item_vec,userid):
    fix_num = 10
    if userid not in user_vec:
        return []
    record = {}
    recom_list = []
    user_vector = user_vec[userid]
    for itemid in item_vec:
        item_vector = item_vec[itemid]
        res = np.dot(user_vector,item_vector)/(np.linalg.norm(user_vector))*(np.linalg.norm(item_vector))
        record[itemid] = res
    for zuhe in sorted(record.iteritems(),key=operator.itemgetter(1),reverse=True)[:fix_num]:
        itemid = zuhe[0]
        score = round(zuhe[1],3)
        recom_list.append((itemid,score))
    return recom_list                                                                            

### 评估推荐结果

In [11]:
def ana_recom_result(train_data,userid,recom_list):
    item_info = get_item_info("../data/movies.csv")
    for data_instance in train_data:
        tmp_userid,itemid,label = data_instance
        if label == 1 and tmp_userid == userid:
            print item_info[itemid]
        print "recom result"
        for zuhe in recom_list:
            print item_info[zuhe[0]]